In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/commonvoice-v24_en-AU.csv
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/commonvoice-v24_en-AU-split.csv
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_39598667.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_181169.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_24831513.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_18173259.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_19501589.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_19515696.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_478602.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files/common_voice_en_22204556.mp3
/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/au

In [2]:
!pip -q install -U transformers datasets evaluate jiwer accelerate soundfile

In [3]:
import os
import re
import pandas as pd
import numpy as np
import torch

from datasets import Dataset, DatasetDict, Audio
import evaluate
from transformers import WhisperProcessor, WhisperForConditionalGeneration

DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
DTYPE  = torch.float16 if torch.cuda.is_available() else torch.float32

print("Device:", DEVICE, "| dtype:", DTYPE)

# ====== Set your dataset root folder here ======
# Example if you uploaded it as a Kaggle Dataset:
# ROOT = "/kaggle/input/commonvoice-v24-en-au/"
ROOT = "/kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU"  # <-- CHANGE THIS

AUDIO_DIR  = os.path.join(ROOT, "audio_files")
CSV_MAIN   = os.path.join(ROOT, "commonvoice-v24_en-AU.csv")
CSV_SPLIT  = os.path.join(ROOT, "commonvoice-v24_en-AU-split.csv")

assert os.path.isdir(AUDIO_DIR), f"Missing audio_files folder: {AUDIO_DIR}"
assert os.path.isfile(CSV_MAIN),  f"Missing main csv: {CSV_MAIN}"
assert os.path.isfile(CSV_SPLIT), f"Missing split csv: {CSV_SPLIT}"

print("Found:", AUDIO_DIR)
print("Found:", CSV_MAIN)
print("Found:", CSV_SPLIT)

Device: cuda | dtype: torch.float16
Found: /kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/audio_files
Found: /kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/commonvoice-v24_en-AU.csv
Found: /kaggle/input/mozilla-commonvoice/commonvoice-v24_en-AU/commonvoice-v24_en-AU-split.csv


In [4]:
df_main  = pd.read_csv(CSV_MAIN)
df_split = pd.read_csv(CSV_SPLIT)

print("Main CSV shape:", df_main.shape)
print("Split CSV shape:", df_split.shape)

print("\nMain columns:\n", df_main.columns.tolist())
print("\nSplit columns:\n", df_split.columns.tolist())

df_main.head()

Main CSV shape: (55673, 15)
Split CSV shape: (55673, 15)

Main columns:
 ['Unnamed: 0', 'client_id', 'path', 'sentence_id', 'sentence', 'sentence_domain', 'up_votes', 'down_votes', 'age', 'gender', 'accents', 'variant', 'locale', 'segment', 'duration_ms']

Split columns:
 ['Unnamed: 0', 'client_id', 'path', 'sentence_id', 'sentence', 'sentence_domain', 'up_votes', 'down_votes', 'age', 'gender', 'accents', 'variant', 'locale', 'segment', 'duration_ms']


Unnamed: 0                                          client_id  \
0         182  0621ad6390e651ff1e39b23f74e8d624bd8ba0957d6a19...   
1         725  18bea6bb076cd9638518d93b4af353c3c329d059789e11...   
2         885  1db7f61c407a3cdce51e21ae1871ef9ae3ed74d79415ba...   
3         984  2144a6feb6a906b220cbba00f37b56084bd2d60cce773e...   
4        1021  22b4048e01f359c779cf9a692f5da7512bfd7ef8c9fff2...   

                           path  \
0  common_voice_en_30513358.mp3   
1  common_voice_en_43618790.mp3   
2  common_voice_en_21099981.mp3   
3  common_voice_en_39588772.mp3   
4  common_voice_en_37211578.mp3   

                                         sentence_id  \
0  1f08423cd2153df43fb7c18ddd24edfea7be733046c26d...   
1  fe3f016c86bea44ab149bc2537de58f16051d8274099a7...   
2  48e620d96dda152eeec48e28f7b0dde29625591bdc44cd...   
3  e3d037f2c263d604b0bb1ef837b1fc7ee7f80d5336031c...   
4  cdfb0356e09201212c123e83ab27e43c48a62b6ce8520d...   

                                            sentence sentence_domain  \
0  Princess Vilas herself also contributed person...             NaN   
1     He has also served in the Chamber of Deputies.             NaN   
2  Most of his subjects were found in Devon and C...             NaN   
3  Shots rang out as they fled towards the Austri...             NaN   
4  The system is based on electromagnetic induction.             NaN   

   up_votes  down_votes       age          gender             accents  \
0         4           0     teens  male_masculine  Australian English   
1         2           0       NaN             NaN  Australian English   
2         2           0  thirties  male_masculine  Australian English   
3         2           0       NaN             NaN  Australian English   
4         2           0       NaN             NaN  Australian English   

   variant locale segment  duration_ms  
0      NaN     en     NaN     7.387500  
1      NaN     en     NaN     6.307500  
2      NaN     en     NaN     7.949625  
3      NaN     en     NaN     5.515500  
4      NaN     en     NaN     4.055656

In [6]:
# ===== Cell 4 (REPLACE) — Merge + pick transcript + build audio_path =====

# Merge on 'path' since you have it
assert "path" in df_main.columns, "df_main must contain 'path'"
assert "path" in df_split.columns, "df_split must contain 'path'"

df = df_main.merge(df_split, on="path", how="inner")
print("Merged shape:", df.shape)

# Pick transcript column: prefer sentence_x, else sentence_y
if "sentence_x" in df.columns:
    text_col = "sentence_x"
elif "sentence_y" in df.columns:
    text_col = "sentence_y"
else:
    raise ValueError("No transcript column found. Expected 'sentence_x' or 'sentence_y' after merge.")

audio_col = "path"  # audio file name

print("Transcript column:", text_col)
print("Audio column:", audio_col)

# Build absolute audio path
df["audio_path"] = df[audio_col].astype(str).apply(lambda x: os.path.join(AUDIO_DIR, x))

# Keep only existing audio files
exists_mask = df["audio_path"].apply(os.path.isfile)
missing = (~exists_mask).sum()
print("Missing audio files:", missing)

df = df[exists_mask].copy()
print("After keeping existing audio:", df.shape)

df[["audio_path", text_col]].head()

Merged shape: (55673, 29)
Transcript column: sentence_x
Audio column: path
Missing audio files: 0
After keeping existing audio: (55673, 30)


audio_path  \
0  /kaggle/input/mozilla-commonvoice/commonvoice-...   
1  /kaggle/input/mozilla-commonvoice/commonvoice-...   
2  /kaggle/input/mozilla-commonvoice/commonvoice-...   
3  /kaggle/input/mozilla-commonvoice/commonvoice-...   
4  /kaggle/input/mozilla-commonvoice/commonvoice-...   

                                          sentence_x  
0  Princess Vilas herself also contributed person...  
1     He has also served in the Chamber of Deputies.  
2  Most of his subjects were found in Devon and C...  
3  Shots rang out as they fled towards the Austri...  
4  The system is based on electromagnetic induction.

In [ ]:
df.columns

In [7]:
def normalize_text(s: str) -> str:
    s = str(s).lower().strip()
    # remove punctuation except apostrophes (optional)
    s = re.sub(r"[^a-z0-9'\s]", " ", s)
    s = re.sub(r"\s+", " ", s).strip()
    return s

df["text"] = df[text_col].apply(normalize_text)

# drop empty transcripts
df = df[df["text"].str.len() > 0].copy()

print("After cleaning text:", df.shape)
df[["audio_path", "text"]].head()

After cleaning text: (55673, 31)


audio_path  \
0  /kaggle/input/mozilla-commonvoice/commonvoice-...   
1  /kaggle/input/mozilla-commonvoice/commonvoice-...   
2  /kaggle/input/mozilla-commonvoice/commonvoice-...   
3  /kaggle/input/mozilla-commonvoice/commonvoice-...   
4  /kaggle/input/mozilla-commonvoice/commonvoice-...   

                                                text  
0  princess vilas herself also contributed person...  
1      he has also served in the chamber of deputies  
2  most of his subjects were found in devon and c...  
3  shots rang out as they fled towards the austri...  
4   the system is based on electromagnetic induction

In [ ]:
df.columns

In [8]:
# ===== Cell 6 (REPLACE) — Create train/validation/test splits =====
from sklearn.model_selection import train_test_split

# Use only what we need
df2 = df[["audio_path", "text"]].copy()

# Remove any empty rows just in case
df2 = df2[df2["text"].astype(str).str.len() > 0].copy()

print("Total usable rows:", len(df2))

# 5% test, 5% val (from remaining)
train_df, test_df = train_test_split(
    df2,
    test_size=0.05,
    random_state=42,
    shuffle=True
)

train_df, val_df = train_test_split(
    train_df,
    test_size=0.05263,  # 0.05263 * 95% ≈ 5% of total
    random_state=42,
    shuffle=True
)

train_df = train_df.reset_index(drop=True)
val_df   = val_df.reset_index(drop=True)
test_df  = test_df.reset_index(drop=True)

print("Train/Val/Test:", len(train_df), len(val_df), len(test_df))

# (Optional but recommended for Kaggle P100 inference speed)
# Keep full train, but cap val/test for faster WER iteration.
VAL_CAP  = min(2000, len(val_df))
TEST_CAP = min(2000, len(test_df))

val_df  = val_df.iloc[:VAL_CAP].reset_index(drop=True)
test_df = test_df.iloc[:TEST_CAP].reset_index(drop=True)

print("After caps -> Val/Test:", len(val_df), len(test_df))

Total usable rows: 55673
Train/Val/Test: 50105 2784 2784
After caps -> Val/Test: 2000 2000


In [14]:
from datasets import Dataset, DatasetDict

ds = DatasetDict({
    "train": Dataset.from_pandas(train_df),
    "validation": Dataset.from_pandas(val_df),
    "test": Dataset.from_pandas(test_df),
})

ds

DatasetDict({
    train: Dataset({
        features: ['audio_path', 'text'],
        num_rows: 50105
    })
    validation: Dataset({
        features: ['audio_path', 'text'],
        num_rows: 2000
    })
    test: Dataset({
        features: ['audio_path', 'text'],
        num_rows: 2000
    })
})

In [20]:
from transformers import WhisperProcessor, WhisperForConditionalGeneration
import torch

MODEL_NAME = "openai/whisper-small.en"

processor = WhisperProcessor.from_pretrained(MODEL_NAME)
model = WhisperForConditionalGeneration.from_pretrained(MODEL_NAME).to(DEVICE)

# dtype consistency (prevents Half vs Float bias crash)
if DEVICE == "cuda":
    model = model.half()

# English-only model: use forced decoder prompt ids (works fine)
model.config.forced_decoder_ids = processor.get_decoder_prompt_ids(task="transcribe")

print("Loaded:", MODEL_NAME, "| model dtype:", next(model.parameters()).dtype)

Loading weights:   0%|          | 0/479 [00:00<?, ?it/s]

Loaded: openai/whisper-small.en | model dtype: torch.float16


In [23]:
import librosa
import torch

@torch.no_grad()
def transcribe_batch(batch, max_new_tokens=128):
    audio_arrays = []
    for p in batch["audio_path"]:
        y, sr = librosa.load(p, sr=16000)
        audio_arrays.append(y)

    inputs = processor(
        audio_arrays,
        sampling_rate=16000,
        return_tensors="pt"
    )

    input_features = inputs.input_features.to(DEVICE)

    # match model dtype (prevents Half/Float crash)
    model_dtype = next(model.parameters()).dtype
    input_features = input_features.to(model_dtype)

    predicted_ids = model.generate(
        input_features,
        max_new_tokens=max_new_tokens,
        do_sample=False,
        num_beams=1
    )

    preds = processor.batch_decode(predicted_ids, skip_special_tokens=True)
    preds = [normalize_text(p) for p in preds]
    batch["pred_text"] = preds
    return batch

In [12]:
!pip install torchcodec

In [24]:
wer_metric = evaluate.load("wer")

N_TEST = min(2000, len(ds["test"]))
test_small = ds["test"].select(range(N_TEST))

print("Evaluating on test samples:", len(test_small))

test_pred = test_small.map(
    transcribe_batch,
    batched=True,
    batch_size=8,   # if OOM, reduce to 4
)

wer = wer_metric.compute(
    predictions=test_pred["pred_text"],
    references=test_pred["text"]
)

print(f"WER on {N_TEST} samples: {wer:.4f}")

Evaluating on test samples: 2000


Map:   0%|          | 0/2000 [00:00<?, ? examples/s]

Both `max_new_tokens` (=128) and `max_length`(=448) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
A custom logits processor of type <class 'transformers.generation.logits_process.SuppressTokensLogitsProcessor'> has been passed to `.generate()`, but it was also created in `.generate()`, given its parameterization. The custom <class 'transformers.generation.logits_process.SuppressTokensLogitsProcessor'> will take precedence. Please check the docstring of <class 'transformers.generation.logits_process.SuppressTokensLogitsProcessor'> to see related `.generate()` flags.
A custom logits processor of type <class 'transformers.generation.logits_process.SuppressTokensAtBeginLogitsProcessor'> has been passed to `.generate()`, but it was also created in `.generate()`, given its parameterization. The custom <class 'transformers.generation.logits_pr

WER on 2000 samples: 0.0950


In [25]:
for i in [0, 1, 2, 3, 4]:
    print("REF:", test_pred[i]["text"])
    print("PRD:", test_pred[i]["pred_text"])
    print("-" * 80)

REF: she wrote good news
PRD: she writes good news
--------------------------------------------------------------------------------
REF: will you breakfast with me
PRD: will you breakfast with me
--------------------------------------------------------------------------------
REF: it rained heavily last night
PRD: it rained heavily last night
--------------------------------------------------------------------------------
REF: strike while the iron is hot
PRD: strike while the iron is hot
--------------------------------------------------------------------------------
REF: the aldermen however were very slow in paying his bill
PRD: the alderman however were very slow in paying his bill
--------------------------------------------------------------------------------


In [26]:
N_VAL = min(1000, len(ds["validation"]))
val_small = ds["validation"].select(range(N_VAL))

val_pred = val_small.map(
    transcribe_batch,
    batched=True,
    batch_size=8,
)

val_wer = wer_metric.compute(
    predictions=val_pred["pred_text"],
    references=val_pred["text"]
)

print(f"Validation WER on {N_VAL} samples: {val_wer:.4f}")

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Both `max_new_tokens` (=128) and `max_length`(=448) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=128) and `max_length`(=448) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=128) and `max_length`(=448) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=128) and `max_length`(=448) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


Validation WER on 1000 samples: 0.0905


In [27]:
out_df = pd.DataFrame({
    "reference": test_pred["text"],
    "prediction": test_pred["pred_text"],
})
out_path = "/kaggle/working/whisper_small_en_test_predictions.csv"
out_df.to_csv(out_path, index=False)
print("Saved:", out_path)
out_df.head()

Saved: /kaggle/working/whisper_small_en_test_predictions.csv


reference  \
0                                she wrote good news   
1                         will you breakfast with me   
2                       it rained heavily last night   
3                       strike while the iron is hot   
4  the aldermen however were very slow in paying ...   

                                          prediction  
0                               she writes good news  
1                         will you breakfast with me  
2                       it rained heavily last night  
3                       strike while the iron is hot  
4  the alderman however were very slow in paying ...